In [22]:
!pip3 install OpenNMT-py==1.2.0

Defaulting to user installation because normal site-packages is not writeable


In [26]:
import requests

def get_forms(sysID, lang, lemma_tags_set):
    """lemma_tags_set: `[{"lemma": "go", "tags": "V;PST"}, ...]`"""
    
    request_data = {
        "sysID": sysID,
        "lang": lang,
        "data": lemma_tags_set
    }
    response = requests.post('https://test2.kurdinus.com/oracle/GetForms', json=request_data)
    if response.status_code == 200:
        return response.content.decode()
    else:
        return "#FAILED: " + str(response.status_code)

In [27]:
def check_forms(sysID, lang, lemma_form_tags_set):
    """lemma_forms_tags_set: `[{"lemma": "go", "form": "goed", "tags": "V;PST"}, ...]`"""
    
    request_data = {
        "sysID": sysID,
        "lang": lang,
        "data": lemma_form_tags_set
    }
    response = requests.post('https://test2.kurdinus.com/oracle/CheckForms', json=request_data)
    print(response)
    if response.status_code == 200:
        return response.content.decode()
    else:
        return "#FAILED: " + str(response.status_code)

In [28]:
import pandas as pd
import random

file = pd.read_csv('lat.tsv', sep='\t', header=None).values.tolist()

def get_data(rows, function):
    """rows: `[[lemma, form(if checking data), tags], ...]`
    output: `["lemma\\t form\\t tags", ...]`"""

    lemma_forms_tags_set = []
    for row in rows:
        if row in file: file.remove(row)
        lemma_forms_tags_set.append({"lemma": row[0], "form": row[1], "tags": row[-1]})

    oracle_data = function("fumo", "lat", lemma_forms_tags_set).split('\n')[:-1]
    return oracle_data

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x7fda9a77e6e0>>
Traceback (most recent call last):
  File "/home/bitmap4/.local/lib/python3.10/site-packages/ipykernel/ipkernel.py", line 770, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(
KeyboardInterrupt: 


In [ ]:

rows = random.sample(file, 1000)

# split 90-10 into train and dev
oracle_data = get_data(rows, get_forms)
train_data = oracle_data[:int(len(oracle_data)*0.9)]
dev_data = oracle_data[int(len(oracle_data)*0.9):]
print(oracle_data[:5])

['ēmētior\tēmētīris\tV;IND;ACT;PRS;2;SG', 'praeterfluō\tpraeterflueris\tV;IND;PASS;PRS;2;SG', 'impedicō\timpedicāris\tV;IND;PASS;PRS;2;SG', 'adsentior\tadsentītur\tV;IND;ACT;PRS;3;SG', 'dēmōliō\tdēmōliēbant\tV;IND;ACT;PST;IPFV;3;PL']


In [ ]:
def create_data_files(name, data):
    """data: `["lemma\\t form\\t tags", ...]`
    output: `name.src`, `name.tgt` files with the data in this format: `g o # V PST` and `w e n t`"""
    train_src = open(f'data/{name}.src', 'w')
    train_tgt = open(f'data/{name}.tgt', 'w')
    for result in data:
        if type(result) == str: result = result.split('\t')
        if len(result) == 2:
            lemma, tags = result
            word = ''
        else:
            lemma, word, tags = result
        src = ' '.join(list(lemma)) + " # " + ' '.join(tags.split(';'))
        tgt = ' '.join(list(word))
        train_src.write(src + '\n')
        train_tgt.write(tgt + '\n')
    train_src.close()
    train_tgt.close()

In [ ]:
create_data_files('train', train_data)
create_data_files('dev', dev_data)

In [ ]:
!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite

[2024-05-08 01:10:34,788 INFO] Extracting features...
[2024-05-08 01:10:34,793 INFO]  * number of source features: 0.
[2024-05-08 01:10:34,794 INFO]  * number of target features: 0.
[2024-05-08 01:10:34,794 INFO] Building `Fields` object...
[2024-05-08 01:10:34,794 INFO] Building & saving training data...
[2024-05-08 01:10:34,796 WARNING] Shards for corpus train already exist, will be overwritten because `-overwrite` option is set.
[2024-05-08 01:10:34,813 WARNING] Overwrite shards for corpus None
[2024-05-08 01:10:34,850 INFO] Building shard 0.
[2024-05-08 01:10:34,887 INFO]  * saving 0th train data shard to run/data.train.0.pt.
[2024-05-08 01:10:35,168 INFO]  * tgt vocab size: 36.
[2024-05-08 01:10:35,168 INFO]  * src vocab size: 50.
[2024-05-08 01:10:35,181 INFO] Building & saving validation data...
[2024-05-08 01:10:35,185 WARNING] Shards for corpus valid already exist, will be overwritten because `-overwrite` option is set.
[2024-05-08 01:10:35,193 WARNING] Overwrite shards for co

In [ ]:
%%capture cap1 --no-stderr
!onmt_train -data run/data -save_model run/model -encoder_type rnn -rnn_type LSTM -rnn_size 128 -layers 1 -word_vec_size 128 -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2
with open('train.log', 'w') as f:
    f.write(cap1.stdout)

In [ ]:
%%capture cap2 --no-stderr
!onmt_translate -model run/model_step_1200.pt -src data/dev.src -output data/dev.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

In [ ]:
!julia evaluate.jl data/dev.tgt data/dev.hyp

Accuracy: 61 / 100   0.61
Character edit distance 0.91
dēspuentur -> dēspulābuntur
partiuntur -> partiantur
glabrō -> glabrāor
itinerāris -> inēris
perductant -> perdulant
retrōgradiēris -> retradiēris
cōnsipiēbant -> cōnsipiābant
anteviābāmus -> anteviēbāmus
adnūtābit -> adnūtēt
extollentur -> extollēbuntur
īnsidiābor -> īnsidiar
soccitābis -> socitābis
ciuntur -> ciēuntur
heiulābar -> hiulābar
assellābāmur -> asselābāmur
fēriantur -> fēriuntur
petissō -> pessō
abnumerābis -> abnumēberis
posteunt -> postīunt
fruimur -> fruāmur
dēpecīscēbantur -> dēpecīcābantur
paedagōgās -> paedasgās
piscābātur -> piscorrābātur
coniūcundābāminī -> coniābāminī
argūtantur -> argūtābuntur
adfremēbam -> adfremō
cōnscreābiminī -> cōnscrecreminī
cōnscreābor -> cōnscreor
collīneābitis -> collīnēbitis
coūtēbāminī -> cotābāminī
ruīnābis -> ruīnās
stipulāmur -> stulāmur
pandiculor -> pandiculāor
fābulor -> fābulāor
contūtābāmur -> contūtūēbāmur
medēris -> medeorris
trālūcēbātis -> trālūcetis
arborēscēbās -> arb

In [ ]:
import re

def get_sorted(text = None):
    if text==None: 
        with open('pred_scores.log', 'r') as file:
            lines = file.readlines()
    else: lines = text.split('\n')

    data = []
    lemma = ''
    tags = ''
    score = 0
    for i in range(len(lines)):
        if lines[i].startswith('SENT'):
            lemma_tags = re.findall(r'\[\'(.*)\'\]', lines[i])[0]
            lemma, tags = lemma_tags.split('#')
            lemma = lemma.replace("'", '').replace(', ', '')
            tags = tags.replace("'", '').replace(', ', ';')[1:]
        elif lines[i].startswith('PRED SCORE'):
            score = float(lines[i].split(':')[1].strip())
        elif lines[i].startswith('PRED'):
            prediction = lines[i].split(':')[1].strip().replace(' ', '')
            data.append((lemma, prediction, tags, score))

    data.sort(key=lambda x: x[3])
    return data

In [ ]:
%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in incorrect if x not in data]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -encoder_type rnn -rnn_type LSTM -rnn_size 128 -layers 1 -word_vec_size 128 -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

In [ ]:
%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in incorrect if x not in data]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -encoder_type rnn -rnn_type LSTM -rnn_size 128 -layers 1 -word_vec_size 128 -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

In [ ]:
%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in incorrect if x not in data]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -encoder_type rnn -rnn_type LSTM -rnn_size 128 -layers 1 -word_vec_size 128 -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

In [ ]:
%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in incorrect if x not in data]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -encoder_type rnn -rnn_type LSTM -rnn_size 128 -layers 1 -word_vec_size 128 -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

In [ ]:
least_confident

[('impraegnō',
  'impraegraegraegraegraegraegraegraegraegraegrenpraegraegnāberis',
  'V;IND;PASS;FUT;2;SG'),
 ('impraegnō',
  'impraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegraegr',
  'V;IND;PASS;FUT;3;SG'),
 ('superimmineō', 'superimmminet', 'V;IND;ACT;PRS;1;PL'),
 ('disquīrō', 'dissoquitus', 'V;IND;ACT;PRS;3;SG'),
 ('convomō', 'convomeābāmus', 'V;IND;ACT;PST;IPFV;1;PL'),
 ('disquīrō', 'dissuīrāberis', 'V;IND;PASS;FUT;2;SG'),
 ('convomō', 'convormōābam', 'V;IND;ACT;PST;IPFV;1;SG'),
 ('lēnō', 'lēnēmur', 'V;IND;PASS;FUT;1;PL'),
 ('impraegnō', 'impraegraegris', 'V;IND;ACT;PRS;2;SG'),
 ('convomō', 'convomuēbat', 'V;IND;ACT;PST;IPFV;3;SG'),
 ('grassor', 'grassorāminī', 'V;IND;ACT;PRS;2;PL'),
 ('disquīrō', 'dissuīrābāmus', 'V;IND;ACT;PST;IPFV;1;PL'),
 ('convomō', 'convormōābās', 'V;IND;ACT;PST;IPFV;2;SG'),
 ('disquīrō', 'dissoquēbis', 'V;IND;ACT;FUT;2;SG'),
 ('convomō', 'convomōmuēbar', 'V;IND;PASS;PST;IPFV;1;SG'),
 ('convomō', 'convormōābis',

In [ ]:
import subprocess
# now predict all data in `file`
# with open('pred_scores.log', 'w') as f:
#     f.write('')

# print(len(file)//100)
# for i in range(len(file)//100):
#     create_data_files("test", file[100*i : len(file) if 100*(i+1)>len(file) else 100*(i+1)])
#     command = "onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose"
#     process = subprocess.run(command, shell=True)
#     data = process.stdout
#     data = [x[:-1] for x in get_sorted(data)]
#     print(len(data))
#     results += get_data(data, check_forms)
create_data_files("test", file)
command = "onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose"
process = subprocess.run(command, shell=True)
data = process.stdout
data = [x[:-1] for x in get_sorted(data)]
results = get_data(data, check_forms)


/home/bitmap4/.local/lib/python3.10/site-packages/torch/nn/modules/rnn.py:83: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.3 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
[2024-05-08 01:25:14,301 INFO] Translating shard 0.
/home/bitmap4/.local/lib/python3.10/site-packages/onmt/translate/beam_search.py:209: UserWarning: An output with one or more elements was resized since it had shape [150], which does not match the required output shape [30, 5]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at ../aten/src/ATen/native/Resize.cpp:28.)
  torch.mul(self.topk_scores, length_penalty, out=self.topk_log_probs)
[2024-05-08 01:25:14,476 INFO] 
SENT 1: ['i', 'm

<Response [200]>


In [ ]:
with open('predictions', 'w') as f:
    for row in results:
        f.write(row + '\n')

In [ ]:
results

['impraegnō\timpraegnāberis\tV;IND;PASS;FUT;2;SG',
 'impraegnō\timpraegnābitur\tV;IND;PASS;FUT;3;SG',
 'superimmineō\tsuperimminēmus\tV;IND;ACT;PRS;1;PL',
 'disquīrō\tdisquīrit\tV;IND;ACT;PRS;3;SG',
 'convomō\tconvomēbāmus\tV;IND;ACT;PST;IPFV;1;PL',
 'disquīrō\tdisquīrēris\tV;IND;PASS;FUT;2;SG',
 'convomō\tconvomēbam\tV;IND;ACT;PST;IPFV;1;SG',
 'lēnō\tlēnābimur\tV;IND;PASS;FUT;1;PL',
 'impraegnō\timpraegnās\tV;IND;ACT;PRS;2;SG',
 'convomō\tconvomēbat\tV;IND;ACT;PST;IPFV;3;SG',
 'grassor\tgrassāminī\tV;IND;ACT;PRS;2;PL',
 'disquīrō\tdisquīrēbāmus\tV;IND;ACT;PST;IPFV;1;PL',
 'convomō\tconvomēbās\tV;IND;ACT;PST;IPFV;2;SG',
 'disquīrō\tdisquīrēs\tV;IND;ACT;FUT;2;SG',
 'convomō\tconvomēbar\tV;IND;PASS;PST;IPFV;1;SG',
 'convomō\tconvomēs\tV;IND;ACT;FUT;2;SG',
 'foeteō\tfoetētis\tV;IND;ACT;PRS;2;PL',
 'convomō\tconvomēris\tV;IND;PASS;FUT;2;SG',
 'assentior\tassentior\tV;IND;ACT;PRS;1;SG',
 'impraegnō\timpraegnor\tV;IND;PASS;PRS;1;SG',
 'petessō\tpetessimur\tV;IND;PASS;PRS;1;PL',
 'convomō\tco

In [ ]:
!curl -X 'POST' \
  'https://test2.kurdinus.com/Oracle/GetAnalysis?sysID=fumo&lang=lat' \
  -H 'accept: */*' \
  -H 'Content-Type: multipart/form-data' \
  -F 'file=@predictions'